### mudraw

In [8]:
import subprocess
import re
import os
from os.path import expanduser

home = expanduser("~")
path = os.path.join(home, 'Bureau')


def findPdfs():
    #p = subprocess.Popen(['ls', '*.pdf'], shell=True, cwd=cwd, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    #out, err = p.communicate()
    #out = out.decode('utf-8')
    #return out.splitlines()
    files = [f for f in os.listdir(path) if os.path.isfile(os.path.join(path, f))]
    return files

def getPdfText(pdf):
    p = subprocess.Popen(['mudraw', '-F', 'html', pdf], cwd=path, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    out, err = p.communicate()
    out = out.decode('utf-8')
    return out

def getPdfFonts(pdf):
    pdftext = getPdfText(pdf)
    #print(pdftext)

    i = 0
    fonts = []
    #regex = (r'<style>(.+?)</style>')
    while True:
        regex = ('span.s{}'.format(i) + '{(.+?)}')
        pattern = re.compile(regex)
        font = re.findall(pattern, pdftext)
        if len(font)>0:
            fonts.append(font[0])
        else:
            break
        i += 1
    print(fonts)
    
    font_sizes = []
    for i in range(len(fonts)):
        font = fonts[i]
        start = font.find('font-size:') + 10
        end = font.find('pt;', start)
        font_size = float(font[start:end])
        font_sizes.append(font_size)
    print(font_sizes)

    
def getPdfTitle(pdf):
    pdftext = getPdfText(pdf)
    print(pdftext)

    regex = ('<span class="s0">(.+?)</span>')
    pattern = re.compile(regex)
    title = re.findall(pattern, pdftext)
    if isinstance(title, list):
        return title[0]
    else:
        return None


pdfs = findPdfs()
print(pdfs)

getPdfFonts(pdfs[-1]) 
titles = getPdfTitle(pdfs[-1])
print(titles)



['2015_Nonlinear Communication System With\nHarmonic Diversity.pdf', '1709.06972.pdf', '2016_Multifunctional Transceiver for Future Radar\nSensing and Radio Communicating\nData-Fusion Platform.pdf']
['font-family:"FormataOTF-Reg";font-size:6.9738pt;', 'font-family:"GiovanniStd-BookItalic";font-size:5.9776pt;font-style:italic;', 'font-family:"FormataOTFCond-Md";font-size:21.9178pt;', 'font-family:"FormataOTFMd";font-size:9.863pt;', 'font-family:"TimesLTStd-Roman";font-size:6.5753pt;', 'font-family:"TimesLTStd-Roman";font-size:7.6712pt;', 'font-family:"FormataOTF-Bold";font-size:9.9626pt;font-weight:bold;', 'font-family:"TimesLTStd-Roman";font-size:9.9626pt;', 'font-family:"FormataOTF-Bold";font-size:8.9664pt;font-weight:bold;', 'font-family:"FormataOTF-Reg";font-size:5.9776pt;', 'font-family:"FormataOTF-Reg";font-size:5.9776pt;', 'font-family:"FormataOTFMdIt";font-size:8.9664pt;font-style:italic;', 'font-family:"TimesLTStd-Italic";font-size:9.9626pt;font-style:italic;', 'font-family:"Ti

In [40]:

p = subprocess.Popen(['ls', '--help'], stdout=subprocess.PIPE, stderr=subprocess.PIPE)
out, err = p.communicate()
out = out.decode('utf-8')
print(out)


Utilisation : ls [OPTION]... [FICHIER]...
Afficher des renseignements sur les FILEs (du répertoire actuel par défaut).
Trier les entrées alphabétiquement si aucune des options -cftuvSUX ou --sort
ne sont utilisées.

Les arguments obligatoires pour les options longues le sont aussi pour les
options courtes.
  -a, --all                  ne pas ignorer les entrées débutant par .
  -A, --almost-all           ne pas inclure . ou .. dans la liste
      --author               avec -l, afficher l'auteur de chaque fichier
  -b, --escape               afficher les caractères non graphiques avec des
                               protections selon le style C
      --block-size=TAILLE    convertir les tailles en TAILLE avant de les
                               afficher. Par exemple, « --block-size=M » affiche
                               les tailles en unités de 1 048 576 octets ;
                               consultez le format de TAILLE ci-dessous
  -B, --ignore-backups       ne pas inclur

### pdfminer

In [ ]:
## pdfminer: python 3 not supported

from pdfminer.converter import TextConverter
from pdfminer.layout import LAParams
from pdfminer.pdfinterp import PDFResourceManager, PDFPageInterpreter
from pdfminer.pdfpage import PDFPage
import StringIO


def convert_pdf(filename, filename_out=None):
    rsrcmgr = PDFResourceManager()
    retstr = StringIO.StringIO()
    if filename_out!=None:
        retstr = file(filename_out, 'w')
    codec = 'utf-8'
    password = ''
    pagenos = set()
    maxpages = 0
    # output option
    outfile = None
    outtype = None
    imagewriter = None
    rotation = 0
    layoutmode = 'normal'
    codec = 'utf-8'
    pageno = 1
    scale = 1
    caching = True
    showpageno = True
    laparams = LAParams()
    device = TextConverter(rsrcmgr, retstr, codec=codec)

    fp = file(filename, 'rb')
    interpreter = PDFPageInterpreter(rsrcmgr, device)
    #interpreter.process_pdf(rsrcmgr, device, fp)
    for page in PDFPage.get_pages(fp, pagenos,
                                  maxpages=maxpages, password=password,
                                  caching=caching, check_extractable=True):
        page.rotate = (page.rotate+rotation) % 360
        interpreter.process_page(page)
    fp.close()
    device.close()

    if filename_out==None:
        str = retstr.getvalue()
        retstr.close()
        return str
    else:
        retstr.close()
        return retstr

filename = 'file.pdf'
pdf = convert_pdf(filename)

print(pdf)


In [1]:
from PyPDF2 import PdfFileWriter, PdfFileReader

filename = 'file.pdf'

def getDataUsingPyPdf2(filename):
    pdf = PdfFileReader(open(filename, "rb"))
    content = ""

    n_pages = pdf.getNumPages()
    for i in range(n_pages):
        extractedText = pdf.getPage(i).extractText()
        content +=  extractedText + "\n"

    #content = " ".join(content.replace("\xa0", " ").strip().split())
    return content

getDataUsingPyPdf2(filename)


',StudentMember,IEEE,Member,IEEE,Fellow,IEEE,Fellow,IEEEAbstractŠ\n\n\n\nIndexTermsŠ\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\netal.\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\netal.\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\netal.\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\netal.\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\nIRETrans.AntennasPropag.IEEETrans.Microw.TheoryTech.J.Appl.Phys.IEEETrans.Microw.TheoryTech.Electron.Lett.AEUŠInt.J.Electron.Commun.IEEETrans.Microw.TheoryTech.Proc.IEEEIEEEAntennasPropag.Mag.\nIEEEAntennasWire-lessPropag.Lett.\nIEEETrans.Microw.TheoryTech.\nIEEETrans.AntennasPropag.\nIEEETrans.Microw.TheoryTech.Proc.IEEEAn-tennasandPropagationSoc.Int.Symp.\nIEEEAntennasWirelessPropag.Lett.\nIEEETrans.AntennasPropag.IEEETrans.An-tennasPropag.IEEETrans.An-tennasPropag.Int.J.Elect.Electron.Eng.IEEETrans.AntennasPropag.\nIEEETr

In [2]:
from PyPDF2 import PdfFileWriter, PdfFileReader

pdf = PdfFileReader('file.pdf')

info = pdf.getDocumentInfo()
print('info:', info)
print('title:', info.title)

n_pages = pdf.getNumPages()
print('number of pages: ', n_pages)

fields = pdf.getFields()
print('fields:', fields)

name_dists = pdf.getNamedDestinations()
#print('name distinations:', name_dists)

outlines = pdf.getOutlines()
print('outlines:', outlines)

metadata = pdf.getXmpMetadata()
print('metadata:', metadata)

print(metadata.dc_date)
print(metadata.dc_language)
print(metadata.dc_title)


info: {'/CreationDate': "D:20150226213322-05'00'", '/ModDate': "D:20150302062916-05'", '/Title': 'untitled', '/Producer': 'Acrobat Distiller 9.0.0 (Windows)'}
title: untitled
number of pages:  10
fields: None
outlines: []
metadata: <PyPDF2.xmp.XmpInformation object at 0x7f91911267f0>
[]
[]
{'x-default': 'untitled'}
